In [1]:
import tensorflow as tf
from tensorflow import keras
from keras.models import load_model
import numpy as np
import pyaudio
import time
import librosa
import wave
import queue
import IPython.display as ipd
from IPython.display import display, Audio
import soundfile as sf
import os
import threading

os.environ["KMP_DUPLICATE_LIB_OK"]="TRUE"


In [2]:
# Định nghĩa các hằng số
RATE = 16000
CHUNK = 1024
FORMAT = pyaudio.paInt16
CHANNELS = 1
n_times_1s = int(RATE / CHUNK * 1)  # Number of iterations to record 1 second
n_times_145s = int(RATE*1.5/ CHUNK )  # Number of iterations to record 1 second
predict_mode = False
p = pyaudio.PyAudio()

In [3]:
def features_extractor_1s(file_name):
    audio,sample_rate  = librosa.load(file_name, sr=16000, mono=True)
    mfcc = librosa.feature.mfcc(y=audio, sr=sample_rate, n_mfcc=40) ## Apllying mfcc
    mfcc_processed = np.mean(mfcc.T, axis=0) ## some pre-processing
    return mfcc_processed

In [4]:
# def features_extractor_145s(file_name):
#     audio,sample_rate  = librosa.load(file_name, sr=16000, mono=True)
#     mel = mfcc(audio,sample_rate, nfilt=26, numcep=26, nfft=512)
#     imarray = np.resize(mel, (250, 26))
#     return imarray

In [5]:
# Hàm trích xuất đặc trưng MFCC
def features_extractor_145s(file_name):
    audio, sample_rate = librosa.load(file_name,sr=16000, mono=True)
    frame_length = int(0.025 * sample_rate)
    hop_length = int(0.01 * sample_rate)
    n_fft = 2 ** int(np.ceil(np.log2(frame_length)))
    mfcc = librosa.feature.mfcc(y=audio, sr=sample_rate, n_fft=n_fft, hop_length=hop_length, n_mfcc=13)
    desired_size = 150
    mfccs = np.zeros((13,desired_size))
    mfccs[:, :min(desired_size, mfcc.shape[1])] = mfcc[:, :min(desired_size, mfcc.shape[1])]
    delta_mfccs = librosa.feature.delta(mfccs)
    delta2_mfccs = librosa.feature.delta(mfccs, order=2)
    mfccs_features = np.concatenate((mfccs, delta_mfccs, delta2_mfccs))
    mfccs_features = np.transpose(mfccs_features)

    return mfccs_features

In [6]:
def mic_check_1s(file_name):
    return 0

In [7]:
# Hàm dự đoán số 
def mic_check_145s(file_name):
    print(1)
    mfccs_features = features_extractor_145s(file_name)
    print(1)
    # print(mfccs_features.shape())
    # data = mfccs_features
    data = np.stack(mfccs_features)
    data = np.reshape(data,(1,150,39))
    pre_test = model_145s.predict(data, verbose=0)
    print(pre_test)
    s=0
    result = 0
    for i in pre_test[0]:
        if i > 9e-1:
            result = i
            predict_mode = True
            break
        s=s+1
    # s = np.argmax(pre_test)
    # result = pre_test[s]
    if s == 0:
        print("Predict: Batdieuhoa")
        display(Audio(get_file_path('Response','Batdieuhoa.wav'), rate=16000, autoplay=True))
    elif s == 1:
        print("Predict: Tatdieuhoa")
        display(Audio(get_file_path('Response','Tatdieuhoa.wav'), rate=16000, autoplay=True))
    elif s == 2:
        print("Predict: Tang1do")
        display(Audio(get_file_path('Response','Tang1do.wav'),  rate=16000,autoplay=True))
    # elif s == 3:
    #     print("Predict: Tang2do")
    # elif s == 4:
    #     print("Predict: Tang3do")
    elif s == 3:
        print("Predict: Giam1do")
        display(Audio(get_file_path('Response','Giam1do.wav'), rate=16000, autoplay=True))
    # elif s == 5:
    #     print("Predict: Giam2do")
    # elif s == 7:
    #     print("Predict: Giam3do")
    elif s == 4:
        print("Predict: Bat26do")
        display(Audio(get_file_path('Response','Bat26do.wav'), rate=16000, autoplay=True))
    elif s == 5:
        print("Predict: Silent")
    else:
        print("Unrecognizable")
    print('Reliability: %.2f %%' %(result*100.00))
    display(Audio(file_name))
    if s < 5: 
        time.sleep(1)
    
    
#         print('Reliability: %.2f %%' %(result*100.00))
#         display(Audio(file_name))
    

In [8]:
# Hàm của luồng 1
def record_audio_145s(file_number, stream):
    print(f"Recording audio for file {file_number}...")
    frames = []
    for i in range(n_times_145s):
        # Lấy một khung dữ liệu
        data = stream.read(CHUNK)
        frames.append(data)
    # Lưu file âm thanh vào file wav
    filename =  "speech_{}".format(file_number)+".wav"
    print(filename)
    with wave.open(filename, 'wb') as wf:
        wf.setnchannels(CHANNELS)
        wf.setsampwidth(p.get_sample_size(FORMAT))
        wf.setframerate(RATE)
        wf.writeframes(b''.join(frames))
    print(filename)
    return filename

In [9]:
# Hàm của luồng 1
def record_audio():
    print("Recording audio...")
    global predict_mode
    #Khởi tạo Audio
    stream = p.open(format=FORMAT,
                    channels=1,
                    rate=RATE,
                    input=True,
                    frames_per_buffer=CHUNK)
    for i in range(100):
        speech = record_audio_145s(i, stream)
        mic_check_145s(speech)
        print(1)
        !del {speech}
    
    # Đóng stream và thoát khỏi PyAudio
    stream.stop_stream()
    stream.close()
    p.terminate()

    
      
    

In [10]:

def get_file_paths_in_folder(folder_path):
    # Kiểm tra xem đường dẫn thư mục có tồn tại không
    if not os.path.exists(folder_path):
        return "Thư mục không tồn tại"
    
    # Lấy danh sách tên file trong thư mục
    files = os.listdir(folder_path)
    
    # Lọc ra chỉ các tên file (không phải thư mục) và kết hợp với đường dẫn thư mục
    file_paths = [os.path.join(folder_path, file_name) for file_name in files if os.path.isfile(os.path.join(folder_path, file_name))]
    
    return file_paths

In [11]:
def get_file_path(folder,file_name):
    # Lấy đường dẫn đến thư mục làm việc hiện tại trong Jupyter
    current_directory = os.getcwd()

    # Đường dẫn đến thư mục chứa tệp mô hình "H5"
    h5_folder_path = os.path.join(current_directory, folder)

    # Đường dẫn đến tệp mô hình được chỉ định
    file_path = os.path.join(h5_folder_path, file_name)

    return file_path


In [12]:
# model_145s = load_model("add_x3_bg_9_512.h5", compile=False)
# model_145s = load_model("check_5.h5", compile=False)
# model_145s = load_model("check_7_2000.h5", compile=False)


# model_145s = load_model(get_file_path("H5","AN_Rain.h5"), compile=False)

model_145s = load_model(get_file_path("H5","Train_True_150_29_LSTM.h5"), compile=False)

# Au_AN_Rain


In [13]:
record_audio()

Recording audio...
Recording audio for file 0...
speech_0.wav
speech_0.wav
1
1
[[3.6056414e-18 5.2198788e-21 4.4646192e-14 1.3479474e-17 4.7266167e-18
  1.0000000e+00]]
Predict: Silent
Reliability: 100.00 %


1
Recording audio for file 1...
speech_1.wav
speech_1.wav
1
1
[[1.4050274e-16 2.0357018e-18 1.7300035e-13 4.4221126e-16 3.2634346e-17
  1.0000000e+00]]
Predict: Silent
Reliability: 100.00 %


1
Recording audio for file 2...
speech_2.wav
speech_2.wav
1
1
[[7.7028262e-06 6.9364683e-06 4.8131046e-09 2.1067372e-08 3.0639054e-08
  9.9998534e-01]]
Predict: Silent
Reliability: 100.00 %


1
Recording audio for file 3...
speech_3.wav
speech_3.wav
1
1
[[2.4597758e-15 2.8405161e-18 3.1437513e-14 2.2049371e-15 7.7040942e-15
  1.0000000e+00]]
Predict: Silent
Reliability: 100.00 %


1
Recording audio for file 4...
speech_4.wav
speech_4.wav
1
1
[[9.4717550e-01 2.3421789e-04 7.4300268e-09 1.9072961e-10 1.2633305e-05
  5.2577630e-02]]
Predict: Batdieuhoa


...

1
Recording audio for file 66...
speech_66.wav
speech_66.wav
1
1
[[5.1269597e-17 8.4087343e-18 6.9931165e-13 5.0791140e-16 2.5175947e-18
  1.0000000e+00]]
Predict: Silent
Reliability: 100.00 %


1
Recording audio for file 67...
speech_67.wav
speech_67.wav
1
1
[[2.6015480e-14 9.8604819e-17 2.3391159e-12 4.5093652e-16 3.5644539e-16
  1.0000000e+00]]
Predict: Silent
Reliability: 100.00 %


1
Recording audio for file 68...
speech_68.wav
speech_68.wav
1
1
[[2.9009788e-15 5.1838539e-17 1.7354087e-11 7.0116913e-14 2.1090443e-15
  1.0000000e+00]]
Predict: Silent
Reliability: 100.00 %


1
Recording audio for file 69...


KeyboardInterrupt: 